In [1]:
import pandas as pd
import geopandas
from shapely.geometry import Polygon, LineString, Point
from shapely.wkt import dumps, loads
from sqlalchemy import create_engine
import config
import plotly.express as px
import plotly.graph_objs as go
from shapely.ops import nearest_points

In [2]:
engine = create_engine(f'{config.engine}://{config.login}:{config.password}@{config.ip}:{config.port}/{config.name_bd}')
conn = engine.connect()

df = pd.read_sql("SELECT *  FROM records_pk1 WHERE records_pk1.sfn='1324033933112909825.rps' AND records_pk1.fnum=16" ,conn)
df['ord km'] = df['ord'] / 1000
df['dfb km'] = df['dfb'] / 1000

df = df.sort_values('rn')


In [19]:
gdf = geopandas.read_file('railway-line.shp')
gdf = gdf.loc[gdf['RAILWAY'] == 'rail']
df = df.drop_duplicates(['gps_lat','gps_lon'])


# Получение расстояния до железных дорог

In [20]:

from numpy import NaN

res_df = pd.DataFrame({'gps_lon':[], 'gps_lat':[], 'rn':[], 'time':[],'distance':[]})

def is_railway(row):
    gdf = globals()['gdf']
    point = dumps(Point(row['gps_lon'], row['gps_lat']), rounding_precision=6)
    distance = gdf.distance(loads(point))
    # print(f"{distance.idxmin()} : {distance.min()}, {( row['gps_lon'], row['gps_lat'])}")
    if distance.min() < 3:
        series = pd.Series({'gps_lon': row['gps_lon'], 
                       'gps_lat':      row['gps_lat'],
                       'rn':           row['rn'],
                       'time':         row['time'],
                       'distance':     f"{distance.min()}" 
                       })
        globals()['res_df'] = pd.concat([res_df, series.to_frame().T])
df[['gps_lat','gps_lon','rn','time']].iloc[:1000].apply(is_railway, axis=1)


C:\Users\patri\AppData\Local\Temp\ipykernel_16080\1891814156.py:8: UserWarning:

Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


C:\Users\patri\AppData\Local\Temp\ipykernel_16080\1891814156.py:8: UserWarning:

Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


C:\Users\patri\AppData\Local\Temp\ipykernel_16080\1891814156.py:8: UserWarning:

Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


C:\Users\patri\AppData\Local\Temp\ipykernel_16080\1891814156.py:8: UserWarning:

Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before th

26022    None
26267    None
26338    None
26342    None
166      None
         ... 
51694    None
25459    None
78038    None
78051    None
25588    None
Length: 401, dtype: object

In [18]:

chelab = Point(57.897, 59.954)
ekat_coord = Point(56.836, 60.610)
ser = geopandas.GeoSeries(ekat_coord)
geo_frame = geopandas.GeoDataFrame({'col1': ['name1'], 'geometry': [Point(1,2)]})



0
0  POINT (56.83600 60.61000)

In [34]:
import geopandas as gpd
from shapely.geometry import Point
geom=[Point(xy) for xy in ([ 60.572188, 56.974962],[60.601727, 56.844724])]
gdf=gpd.GeoDataFrame(geometry=geom,crs={'init':'epsg:4326'})
gdf.to_crs(epsg=5940,inplace=True)
l=gdf.distance(gdf.shift())
print(l)

0            NaN
1    8351.023975
dtype: float64


c:\Users\patri\OneDrive\Рабочий стол\projects\encrypter-main\venv\lib\site-packages\pyproj\crs\crs.py:141: FutureWarning:

'+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6

c:\Users\patri\OneDrive\Рабочий стол\projects\encrypter-main\venv\lib\site-packages\geopandas\array.py:1406: UserWarning:

CRS not set for some of the concatenation inputs. Setting output's CRS as WGS 84 / EPSG Russia Polar Stereographic (the single non-null crs provided).



# Получение координат железных дорог для визуализациии

In [5]:

# list(gdf.iloc[10101].geometry.coords)
import shapely
railway_coords = pd.DataFrame({'lon':[],'lat':[]})
def get_coords(row):
    if type(row.geometry) == shapely.geometry.multilinestring.MultiLineString:
        for linestring in row.geometry:
            for coord in list(linestring._get_coords()): 
                s = pd.Series({'lon':coord[0], 'lat':coord[1]})
                globals()['railway_coords'] = pd.concat([railway_coords, s.to_frame().T])
    else:
        for coord in list(row.geometry._get_coords()):
            # print(f'x: {coord[0]}, y: {coord[1]}')
            s = pd.Series({'lon':coord[0], 'lat':coord[1]})
            globals()['railway_coords'] = pd.concat([railway_coords, s.to_frame().T], ignore_index=True)
gdf.apply(get_coords, axis=1)
len(df)

C:\Users\patri\AppData\Local\Temp\ipykernel_16080\2877300944.py:6: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for linestring in row.geometry:
C:\Users\patri\AppData\Local\Temp\ipykernel_16080\2877300944.py:6: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for linestring in row.geometry:
C:\Users\patri\AppData\Local\Temp\ipykernel_16080\2877300944.py:6: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for linestring in row.geometry:


78747

In [21]:
fig = go.Figure(go.Scattermapbox(lat=railway_coords['lat'], 
                                 lon=railway_coords['lon'], 
                                )
                )
# fig.add_scattermapbox()
# fig.add_scatter(res_df, x=res_df['gps_lat'])
fig.add_scattermapbox(below="",                       
                        lat=res_df['gps_lat'],
                        lon=res_df['gps_lon'],
                        hovertext =res_df['distance'],
                        )   

fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 55,
    margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [112]:

df = df.sort_values('rn')
coords_df = df[['gps_lat','gps_lon', 'rn', 'time',]]
fig = px.line_mapbox(res_df, lat="gps_lat", lon="gps_lon", hover_name='rn', text='distance', zoom=3, height=500)

fig.update_layout(mapbox_style="open-street-map", mapbox_zoom=4, mapbox_center_lat = 55,
    margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [7]:
df.columns


Index(['sfn', 'fnum', 'bdt', 'rn', 'dfb', 'tfb', 'ord', 'tln', 'tn', 'va',
       'vp', 'dp', 'ptm', 'pur', 'ptc', 'pim', 'dur', 'gc', 'gt', 'gn', 'gr',
       'npbe', 'bc', 'dals', 'dals2', 'dln', 'dIn2', 'dIn3', 'dout', 'dsaut',
       'd1', 'd2', 'd3', 'gps_lat', 'gps_lon', 'errofm', 'km', 'l1', 'l12',
       'l2', 'time', 'ord km', 'dfb km'],
      dtype='object')